In [1]:
import simpy
import random
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from enum import Enum
import os
import shutil
from tqdm import tqdm
import math
from dataclasses import dataclass, field
from typing import List, Union, Dict
import math

# Constants
SEED = 42
ACCESS_COUNT_LIMIT = 1000   # Total time to run the simulation
EXPERIMENT_BASE_DIR = "./experiments/"
TEMP_BASE_DIR = "./.aoi_cache/"

ZIPF_CONSTANT = 2      # Shape parameter for the Zipf distribution (controls skewness) Needs to be: 1< 

# Set random seeds
random.seed(SEED)
np.random.seed(SEED)

os.makedirs(TEMP_BASE_DIR, exist_ok=True)

In [2]:
# Types of cache
class EvictionStrategy(Enum):
    LRU = 1
    RANDOM_EVICTION = 2
    TTL = 3

In [3]:
@dataclass
class DatabaseObject:
    id: int
    data: str
    lambda_value: int
    mu_value: Union[float, None]
    ttl: Union[float, None]

In [4]:
@dataclass
class CacheObject:
    id: int # id of object
    data: DatabaseObject # body of object
    initial_fetch_timer: float # time at which the object was initially pulled into the cache (object_start_time)
    age_timer: float # time at which the object was last pulled into the cache (initial fetch)
    last_access: float # time at which the object was last accesse
    next_refresh: Union[float, None] # scheduled time for the object to be requested (for refresh cache)
    next_expiry: Union[float, None] # scheduled time for the object to be evicted (for ttl cache) (ttl)

In [5]:
# Base class for all cache types
@dataclass
class SimulationConfig:
    db_objects: Union[int, List[DatabaseObject]]
    cache_size: int
    eviction_strategy: EvictionStrategy

    def __post_init__(self):
        if not hasattr(self, 'eviction_strategy') or self.eviction_strategy is None:
            raise ValueError("Eviction strategy must be defined in subclasses.")

    def __repr__(self):
        db_object_count = self.db_objects if isinstance(self.db_objects, int) else len(self.db_objects)
        return f"[{self.__class__.__name__}] Database Object Count: {db_object_count}, Cache Size: {self.cache_size}, Eviction Strategy: {self.eviction_strategy}"
        
    def generate_objects(self):
        if isinstance(self.db_objects, int):
            self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=np.random.zipf(ZIPF_CONSTANT), mu_value=None, ttl=None) 
                for i in range(self.db_objects)
            ]

    def from_file(self, path: str, lambda_column_name: str):
        df = pd.read_csv(path)
        lambdas = df[lambda_column_name]

        self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=lambdas[i], mu_value=None, ttl=None) 
                for i in range(self.db_objects)
            ]
            
# Specific cache type variants
@dataclass
class TTLSimulation(SimulationConfig):
    eviction_strategy: EvictionStrategy = field(default=EvictionStrategy.TTL, init=False)

    def __repr__(self):
        return super().__repr__().replace(super().__class__.__name__, self.__class__.__name__)
        
    def generate_objects(self, fixed_ttl):
        if isinstance(self.db_objects, int):
            self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=np.random.zipf(ZIPF_CONSTANT), mu_value=None, ttl=fixed_ttl) 
                for i in range(self.db_objects)
            ]

    
    def from_file(self, path: str, lambda_column_name: str, ttl_column_name: str):
        df = pd.read_csv(path)
        lambdas = df[lambda_column_name]
        ttls = df[ttl_column_name]

        self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=lambdas[i], mu_value=None, ttl=ttls[i]) 
                for i in range(self.db_objects)
            ]
            
@dataclass
class LRUSimulation(SimulationConfig):
    eviction_strategy: EvictionStrategy = field(default=EvictionStrategy.LRU, init=False)
    
    def __repr__(self):
        return super().__repr__().replace(super().__class__.__name__, self.__class__.__name__)
        

@dataclass
class RandomEvictionSimulation(SimulationConfig):
    eviction_strategy: EvictionStrategy = field(default=EvictionStrategy.RANDOM_EVICTION, init=False)

    
    def __repr__(self):
        return super().__repr__().replace(super().__class__.__name__, self.__class__.__name__)

@dataclass
class RefreshSimulation(TTLSimulation):

    
    def __repr__(self):
        return super().__repr__().replace(super().__class__.__name__, self.__class__.__name__)
        
    def generate_objects(self, fixed_ttl, max_refresh_rate):
        if isinstance(self.db_objects, int):
            self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=np.random.zipf(ZIPF_CONSTANT), mu_value=np.random.uniform(1, max_refresh_rate), ttl=fixed_ttl) 
                for i in range(self.db_objects)
            ]
            
    def from_file(self, path: str, lambda_column_name: str, ttl_column_name: str, mu_column_name: str):
        df = pd.read_csv(path)
        lambdas = df[lambda_column_name]
        ttls = df[ttl_column_name]
        mus = df[mu_column_name]

        self.db_objects = [
                DatabaseObject(id=i, data=f"Generated Object {i}", lambda_value=lambdas[i], mu_value=mus[i], ttl=ttls[i]) 
                for i in range(self.db_objects)
            ]

In [6]:
class Database:
    data: Dict[int, DatabaseObject]
    
    def __init__(self, data: List[DatabaseObject]):
        self.data = {i: data[i] for i in range(len(data))}

    def get_object(self, obj_id):
        # print(f"[{env.now:.2f}] Database: Fetched {self.data.get(obj_id, 'Unknown')} for ID {obj_id}")
        return self.data.get(obj_id, None)

In [7]:
class Cache:
    capacity: int
    eviction_strategy: EvictionStrategy
    cache_size_over_time: List[int]  # To record cache state at each interval
    storage: Dict[int, CacheObject]
    hits: Dict[int, int] # hit counter for each object
    misses: Dict[int, int] # miss counter for each object
    access_count: Dict[int, int] # access counter for each object (should be hit+miss)
    next_request: Dict[int, float] # scheduled time for each object to be requested
    cumulative_age: Dict[int, List[float]] # list of ages of each object at the time it was requested (current time - age_timer)
    cumulative_cache_time: Dict[int, List[float]] # list of total time of each object spent in cache when it was evicted (current time - initial fetch time)
    request_log: Dict[int, List[float]] # list of timestamps when each object was requested
    
    def __init__(self, env, db, simulation_config):
        self.env = env
        self.db = db
        self.capacity = simulation_config.cache_size
        self.eviction_strategy = simulation_config.eviction_strategy
        self.cache_size_over_time = []
        self.storage = {}

        db_object_count = len(self.db.data)
        
        self.hits = {i: 0 for i in range(db_object_count)}
        self.misses = {i: 0 for i in range(db_object_count)}
        self.access_count = {i: 0 for i in range(db_object_count)}
        self.next_request = {i: np.random.exponential(1/self.db.data[i].lambda_value) for i in range(len(self.db.data))}
        self.cumulative_age = {i: [] for i in range(db_object_count)}
        self.cumulative_cache_time = {i: [] for i in range(db_object_count)}
        self.request_log = {i: [] for i in range(db_object_count)}

        
    def get(self, obj_id):
        assert len(self.storage) <= self.capacity, f"Too many objects in cache ({len(self.storage)})."
        # print(f"[{self.env.now:.2f}] Requesting Object {obj_id}... (Cache Size: {len(self.storage)})")

        # Schedule next request
        next_request = self.env.now + np.random.exponential(1/self.db.data[obj_id].lambda_value)
        self.request_log[obj_id].append(next_request)
        self.next_request[obj_id] = next_request
        self.access_count[obj_id] += 1
        # print(f"[{self.env.now:.2f}] Client: Schedule next request for {obj_id}@{next_request:.2f}")
        
        if obj_id in self.storage:
            # Cache hit: Refresh TTL if TTL-Cache
            if self.storage[obj_id].next_expiry:
                assert self.env.now <= self.storage[obj_id].next_expiry, f"[{self.env.now:.2f}] Cache should never hit on an expired cache entry."
                self.storage[obj_id].next_expiry = self.env.now + self.db.data[obj_id].ttl
                    
            # Cache hit: increment hit count and update cumulative age
            self.hits[obj_id] += 1
            age = self.env.now - self.storage[obj_id].age_timer
            self.cumulative_age[obj_id].append(age)
            self.storage[obj_id].last_access = self.env.now

            assert len(self.cumulative_age[obj_id]) == self.access_count[obj_id], f"[{self.env.now:.2f}] Age values collected and object access count do not match."
            # print(f"[{env.now:.2f}] {obj_id} Hit: Current Age {age:.2f} (Average: {sum(self.cumulative_age[obj_id])/len(self.cumulative_age[obj_id]):.2f}) ")
            return self.storage[obj_id]
        else:
            # Cache miss: increment miss count
            self.misses[obj_id] += 1
            self.cumulative_age[obj_id].append(0)
            
            # Cache miss: Add TTL if TTL-Cache
            # When full cache: If Non-TTL-Cache: Evict. If TTL-Cache: Don't add to Cache.
            if len(self.storage) == self.capacity:
                if self.eviction_strategy == EvictionStrategy.LRU:
                    self.evict_oldest()
                elif self.eviction_strategy == EvictionStrategy.RANDOM_EVICTION:
                    self.evict_random()
                elif self.eviction_strategy == EvictionStrategy.TTL:
                    # print(f"[{self.env.now:.2f}] Cache: Capacity reached. Not accepting new request.")
                    return

            # Cache miss: Construct CacheObject from Database Object
            db_object = self.db.get_object(obj_id)
            initial_fetch_timer=self.env.now
            age_timer=self.env.now
            last_access=self.env.now
            next_refresh = (self.env.now + np.random.exponential(1/db_object.mu_value)) if db_object.mu_value is not None else None
            next_expiry = (self.env.now + db_object.ttl) if db_object.ttl is not None else None
            cache_object = CacheObject(id=obj_id, data=db_object, 
                                       initial_fetch_timer=initial_fetch_timer, age_timer=age_timer, 
                                       last_access=last_access,next_refresh=next_refresh, next_expiry=next_expiry
                                      )
            self.storage[obj_id] = cache_object
            
            assert len(self.cumulative_age[obj_id]) == self.access_count[obj_id], f"[{self.env.now:.2f}] Age values collected and object access count do not match."
            # print(f"[{env.now:.2f}] {obj_id} Miss: Average Age {sum(self.cumulative_age[obj_id])/len(self.cumulative_age[obj_id]):.2f} ")
            return self.storage[obj_id]

    def refresh_object(self, obj_id):
        """Refresh the object from the database to keep it up-to-date. TTL is increased on refresh."""
        assert obj_id in self.storage, f"[{self.env.now:.2f}] Refreshed object has to be in cache"
        db_object = self.db.get_object(obj_id)
        age_timer = self.env.now
        next_refresh = self.env.now + np.random.exponential(1/db_object.mu_value)
        # next_expiry = self.env.now + db_object.ttl if db_object.ttl is not None else None

        self.storage[obj_id].data = db_object
        self.storage[obj_id].age_timer = age_timer
        self.storage[obj_id].next_refresh = next_refresh

        # print(f"[{self.env.now:.2f}] Cache: Refreshed object {obj_id}")
        
    def evict_oldest(self):
        """Remove the oldest item from the cache to make space."""
        assert self.capacity == len(self.storage), f"[{self.env.now:.2f}] Expecting cache to be at capacity"
        oldest_id = min(self.storage.items(), key=lambda item: item[1].last_access)[0]
        
        # print(f"[{self.env.now:.2f}] Cache: Evicting oldest object {oldest_id}.")
        self.cumulative_cache_time[oldest_id].append(self.env.now - self.storage[oldest_id].initial_fetch_timer)
        del self.storage[oldest_id]
        
    def evict_random(self):
        """Remove a random item from the cache to make space."""
        assert self.capacity == len(self.storage), f"[{self.env.now:.2f}] Expecting cache to be at capacity"
        random_id = np.random.choice(list(self.storage.keys()))  # Select a random key from the cache
        
        # print(f"[{self.env.now:.2f}] Cache: Evicting random object {random_id}.")
        self.cumulative_cache_time[random_id].append(self.env.now - self.storage[random_id].initial_fetch_timer)
        del self.storage[random_id]
        
    def check_expired(self, obj_id):
        """Remove object if its TTL expired."""
        assert self.storage, f"[{self.env.now:.2f}] Expecting cache to be not empty"
        assert self.env.now >= self.storage[obj_id].next_expiry
        
        # print(f"[{self.env.now:.2f}] Cache: Object {obj_id} expired")
        self.cumulative_cache_time[obj_id].append(self.env.now - self.storage[obj_id].initial_fetch_timer)
        del self.storage[obj_id]

                
    def record_cache_state(self):
        """Record the current cache state (number of objects in cache) over time."""
        self.cache_size_over_time.append((self.env.now, len(self.storage)))

In [8]:
def client_request_process(env, cache, event):
    """Client process that makes requests for objects from the cache."""
    last_print = 0
    with tqdm(total=ACCESS_COUNT_LIMIT, desc="Progress", leave=True) as pbar:
        while True:
            request_id, next_request = min(cache.next_request.items(), key=lambda x: x[1])
            expiry_id = -1
            next_expiry = float('inf')
            refresh_id = -1
            next_refresh = float('inf')

            if cache.storage:
                expiry_id, next_expiry = min(cache.storage.items(), key=lambda x: x[1].next_expiry if x[1].next_expiry is not None else float('inf'))
                next_expiry = cache.storage[expiry_id].next_expiry
                refresh_id, next_refresh = min(cache.storage.items(), key=lambda x: x[1].next_refresh if x[1].next_refresh is not None else float('inf'))
                next_refresh = cache.storage[refresh_id].next_refresh

            events = [
                (request_id, next_request),
                (expiry_id, next_expiry),
                (refresh_id, next_refresh)
            ]

            event_id, event_timestamp = min(events, key=lambda x: x[1] if x[1] is not None else float('inf'))
            
            # if event_id == request_id and event_timestamp == next_request:
            #     print(f"[{env.now:.2f}] Waiting for request...")
            # elif event_id == expiry_id and event_timestamp == next_expiry:
            #     print(f"[{env.now:.2f}] Waiting for expiry until...")
            # elif event_id == refresh_id and event_timestamp == next_refresh:
            #     print(f"[{env.now:.2f}] Waiting for refresh...")

            wait_time = event_timestamp - env.now
            wait_time += math.ulp(wait_time) # Round up

            yield(env.timeout(wait_time))
            if event_id == request_id and event_timestamp == next_request:
                assert env.now >= next_request, f"[{env.now}] Time for request should've been reached for Object {request_id}"
                cache.get(request_id)
            elif event_id == expiry_id and event_timestamp == next_expiry:
                assert env.now >= next_expiry, f"[{env.now}] Time for expiry should've been reached for Object {expiry_id}"
                cache.check_expired(expiry_id)
            elif event_id == refresh_id and event_timestamp == next_refresh:
                assert env.now >= next_refresh, f"[{env.now}] Time for refresh should've been reached for Object {refresh_id}"
                cache.refresh_object(refresh_id)
            else:
                assert False, "Unreachable"

            # For progress bar
            if (int(env.now) % 1) == 0 and int(env.now) != last_print:
                last_print = int(env.now)
                pbar.n = min(cache.access_count.values())
                pbar.refresh()
            
            # Simulation stop condition
            if all(access_count >= ACCESS_COUNT_LIMIT for access_count in cache.access_count.values()):
                print(f"Simulation ended after {env.now} seconds.")
                for obj_id in cache.storage.keys():
                    cache.cumulative_cache_time[obj_id].append(env.now - cache.storage[obj_id].initial_fetch_timer)
                event.succeed()
            
            cache.record_cache_state()

In [9]:
class Simulation:
    def __init__(self, simulation_config: Union[TTLSimulation, LRUSimulation, RandomEvictionSimulation, RefreshSimulation]):
        # Initialize simulation environment
        self.env = simpy.Environment()
        
        # Instantiate components
        self.db = Database(simulation_config.db_objects)
        self.cache = Cache(self.env, self.db, simulation_config)

    def run_simulation(self):
        # Start processes
        # env.process(age_cache_process(env, cache))
        stop_event = self.env.event()
        self.env.process(client_request_process(self.env, self.cache, stop_event))
        
        # Run the simulation
        self.env.run(until=stop_event)
        self.end_time = self.env.now

In [10]:
# Simulate with a Cache that does random evictions, We'll have 100 Database Objects and a Cache Size of 10
# We'll generate lambdas from a zipf distribution
# config = RandomEvictionSimulation(100, 10)
# config.generate_objects()

In [11]:
# Simulate with a Cache that does lru, We'll have 100 Database Objects and a Cache Size of 10
# We'll generate lambdas from a zipf distribution
config = LRUSimulation(100, 10)
config.from_file('./input/2024-12-14/results.csv', 'Lambda')

In [12]:
# Simulate with a Cache that does Refreshes with TTL based eviction, We'll have 100 Database Objects and a Cache Size of 10
# We'll generate lambdas from a zipf distribution. Each object will have a fixed ttl of 1 when its pulled into the cache. Mu for the refresh rate is 10
# config = RefreshSimulation(100, 10)
# config.from_file(path='./input/2024-12-13/output.csv', lambda_column_name='Lambda', ttl_column_name='TTL_2', mu_column_name='u_opt_2')

In [13]:
# Simulate with a Cache that does TTL based eviction, We'll have 100 Database Objects and a Cache Size of 10
# We'll take lambdas from the "lambda" column of the file "../calculated.csv" and the TTLs for each object from the "optimal_TTL" column of the same file.
# config = TTLSimulation(100, 10)
# config.from_file("../calculated.csv", "lambda", "optimal_TTL")

In [14]:
with open(f"{TEMP_BASE_DIR}/simulation_config.txt", 'w') as f:
    f.write(str(config))

In [15]:
%%time

simulation = Simulation(config)
simulation.run_simulation()

Progress:   0%|                                              | 0/1000 [00:00<?, ?it/s]

0.04482947830142957


NameError: name 'error_wait_time' is not defined

In [16]:
cache = simulation.cache
db = simulation.db
simulation_end_time = simulation.end_time
database_object_count = len(db.data)

AttributeError: 'Simulation' object has no attribute 'end_time'

In [ ]:
statistics = []
# Calculate and print hit rate and average age for each object
for obj_id in range(database_object_count):
    if cache.access_count[obj_id] != 0:
        output = ""
        expected_hit_rate = None
        hit_rate = cache.hits[obj_id] / max(1, cache.access_count[obj_id])
        output += f"Object {obj_id}: Hit Rate = {hit_rate:.2f}, "
        if db.data[obj_id].ttl is not None:
            expected_hit_rate = 1-math.exp(-db.data[obj_id].lambda_value*(db.data[obj_id].ttl))
            output += f"Expected Hit Rate = {expected_hit_rate:.2f}, "
        avg_cache_time = sum(cache.cumulative_cache_time[obj_id]) / max(1, simulation_end_time) 
        output += f"Average Time spend in Cache: {avg_cache_time:.2f}, "
        avg_age = sum(cache.cumulative_age[obj_id]) / max(len(cache.cumulative_age[obj_id]), 1)
        output += f"Average Age = {avg_age:.2f}, "
        expected_age = hit_rate / (db.data[obj_id].lambda_value * (1 - pow(hit_rate,2)))
        output += f"Expected Age = {expected_age:.2f}"
        print(output)
        if db.data[obj_id].ttl is not None:
            statistics.append({
                "obj_id": obj_id,
                "hit_rate": hit_rate, 
                "expected_hit_rate": expected_hit_rate, 
                "avg_cache_time":avg_cache_time, 
                "avg_age": avg_age, 
                "expected_age": expected_age
                })
        else:
            statistics.append({
                "obj_id": obj_id,
                "hit_rate": hit_rate, 
                "avg_cache_time":avg_cache_time, 
                "avg_age": avg_age, 
                "expected_age": expected_age
                })

In [ ]:
stats = pd.DataFrame(statistics)
stats.to_csv(f"{TEMP_BASE_DIR}/hit_age.csv",index=False)
stats.drop("obj_id", axis=1).describe().to_csv(f"{TEMP_BASE_DIR}/overall_hit_age.csv")

In [ ]:
expected_hit_rate = None
expected_hit_rate_delta = None

In [ ]:
access_count = pd.DataFrame.from_dict(cache.access_count, orient='index', columns=['access_count'])
hits = pd.DataFrame.from_dict(cache.hits, orient='index', columns=['hits'])
misses = pd.DataFrame.from_dict(cache.misses, orient='index', columns=['misses'])
mu = pd.DataFrame.from_dict({l: db.data[l].mu_value for l in range(database_object_count)}, orient='index', columns=['mu'])
lmbda = pd.DataFrame.from_dict({l: db.data[l].lambda_value for l in range(database_object_count)}, orient='index', columns=['lambda'])

hit_rate = pd.DataFrame(stats['hit_rate'])
hit_rate.index = range(database_object_count)
if 'expected_hit_rate' in stats:
    expected_hit_rate = pd.DataFrame(stats['expected_hit_rate'])
    expected_hit_rate.index = range(database_object_count)
    expected_hit_rate_delta = pd.DataFrame((hit_rate.to_numpy()-expected_hit_rate.to_numpy()), columns=['expected_hit_rate_delta'])
    expected_hit_rate_delta.index = range(database_object_count)
avg_cache_time = pd.DataFrame(stats['avg_cache_time'])
avg_cache_time.index = range(database_object_count)
cache_time_delta = pd.DataFrame((hit_rate.to_numpy()-avg_cache_time.to_numpy()), columns=['cache_time_delta'])
cache_time_delta.index = range(database_object_count)

avg_age = pd.DataFrame(stats['avg_age'])
avg_age.index = range(database_object_count)

ages = {k: str(v) for k,v in cache.cumulative_age.items()}
ages = pd.DataFrame.from_dict(ages, orient='index', columns=['ages'])

merged = access_count.merge(hits, left_index=True, right_index=True).merge(misses, left_index=True, right_index=True) \
    .merge(mu, left_index=True, right_index=True).merge(lmbda, left_index=True, right_index=True) \
    .merge(hit_rate, left_index=True, right_index=True)
if 'expected_hit_rate' in stats:
    merged = merged.merge(expected_hit_rate, left_index=True, right_index=True).merge(expected_hit_rate_delta, left_index=True, right_index=True)
merged = merged.merge(avg_cache_time, left_index=True, right_index=True).merge(cache_time_delta, left_index=True, right_index=True) \
    .merge(avg_age, left_index=True, right_index=True).merge(ages, left_index=True, right_index=True)
merged.to_csv(f"{TEMP_BASE_DIR}/details.csv", index_label="obj_id")
merged

In [ ]:
# Extract recorded data for plotting
times, cache_sizes = zip(*cache.cache_size_over_time)

# Plot the cache size over time
plt.figure(figsize=(30, 5))
plt.plot(times, cache_sizes, label="Objects in Cache")
plt.xlabel("Time (s)")
plt.ylabel("Number of Cached Objects")
plt.title("Number of Objects in Cache Over Time")
plt.legend()
plt.grid(True)
plt.savefig(f"{TEMP_BASE_DIR}/objects_in_cache_over_time.pdf")

plt.show()

In [ ]:
from collections import Counter
# Count occurrences of each number
count = Counter([l.lambda_value for l in db.data.values()])

# Separate the counts into two lists for plotting
x = list(count.keys())  # List of unique numbers
y = list(count.values())  # List of their respective counts

# Plot the data
plt.figure(figsize=(8, 6))
plt.bar(x, y, color='skyblue')

# Adding labels and title
plt.xlabel('Number')
plt.ylabel('Occurrences')
plt.title('Occurance of each lambda in db')
plt.savefig(f"{TEMP_BASE_DIR}/lambda_distribution.pdf")

# Show the plot
plt.show()

In [ ]:
# Plotting lambda against access_count.

plt.figure(figsize=(8, 6))
plt.scatter(merged['lambda'], merged['access_count'], alpha=0.7, edgecolor='k')
plt.title('Lambda vs Access Count', fontsize=14)
plt.xlabel('Lambda', fontsize=12)
plt.ylabel('Access Count', fontsize=12)
plt.grid(alpha=0.3)

plt.savefig(f"{TEMP_BASE_DIR}/lambda_vs_access_count.pdf")
plt.show()

In [ ]:
from collections import Counter
# Count occurrences of each number
count = Counter(np.array([l.mu_value if l.mu_value is not None else 0.0 for l in db.data.values()  ]).round(0))

# Separate the counts into two lists for plotting
x = list(count.keys())  # List of unique numbers
y = list(count.values())  # List of their respective counts

# Plot the data
plt.figure(figsize=(8, 6))
plt.bar(x, y, color='skyblue')

# Adding labels and title
plt.xlabel('Number')
plt.ylabel('Occurrences')
plt.title('Occurance of each mu in db (rounded)')

# Show the plot
plt.show()

In [ ]:
def plot_requests(object_id: int):
    mu = db.mu_values[object_id]
    lmb = db.lambda_values[object_id]
    rq_log = np.array(cache.request_log[object_id])
    df = rq_log[1:] - rq_log[:-1]
    pd.DataFrame(df, columns=[f"{object_id}, mu:{mu:.2f}, lambda: {lmb:.2f}"]).plot()

In [ ]:
def print_rate(object_id: int):
    # Calculate time intervals between consecutive events
    intervals = np.diff(np.array(cache.request_log[object_id]))  # Differences between each event time
    
    # Calculate the rate per second for each interval
    rates = 1 / intervals  # Inverse of the time interval gives rate per second
    
    # Optional: Calculate the average event rate over all intervals
    average_rate = np.mean(rates)
    print("Average event rate per second:", average_rate)
    print("The mu is: ", db.lambda_values[object_id])

In [ ]:
print(config)

In [ ]:
# os.makedirs(EXPERIMENT_BASE_DIR, exist_ok=True)
# folder_name = experiment_name.replace(" ", "_").replace("(", "").replace(")", "").replace(".", "_")
# folder_path = os.path.join(EXPERIMENT_BASE_DIR, folder_name)
# os.makedirs(folder_path, exist_ok=True)


In [ ]:
# file_names = os.listdir(TEMP_BASE_DIR)
    
# for file_name in file_names:
#     shutil.move(os.path.join(TEMP_BASE_DIR, file_name), folder_path)